In [10]:


seed_value= 0

# 1. Set `PYTHONHASHSEED` environment variable at a fixed value
import os
os.environ['PYTHONHASHSEED']=str(seed_value)

# 2. Set `python` built-in pseudo-random generator at a fixed value
import random
random.seed(seed_value)

# 3. Set `numpy` pseudo-random generator at a fixed value
import numpy as np
np.random.seed(seed_value)

# 4. Set `tensorflow` pseudo-random generator at a fixed value
import tensorflow as tf
tf.random.set_seed(seed_value)

# 5. Configure a new global `tensorflow` session
from tensorflow.keras import backend as K
session_conf = tf.compat.v1.ConfigProto(
    intra_op_parallelism_threads=1, 
    inter_op_parallelism_threads=1
)
sess = tf.compat.v1.Session(
    graph=tf.compat.v1.get_default_graph(), 
    config=session_conf
)
tf.compat.v1.keras.backend.set_session(sess)

import pandas as pd
import matplotlib
from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout, BatchNormalization
from sklearn.preprocessing import StandardScaler,MinMaxScaler,RobustScaler
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.callbacks import ModelCheckpoint
from sklearn.metrics import r2_score as r2
from sklearn.metrics import mean_squared_error as mse
np.seterr(all='warn')
import warnings
warnings.filterwarnings('ignore')
%matplotlib inline  


In [11]:
p=pd.read_csv('data.csv')

features = p.drop('I', axis=1).values
X_train, X_test, y_train, y_test = train_test_split(features,p['I'].values,

                                                    test_size=0.15,random_state=0)
scale = StandardScaler()
scale = scale.fit(X_train)
X_train = scale.transform(X_train)
X_test = scale.transform(X_test)

def r_square(y_true, y_pred):
    
    SS_res =  K.sum(K.square(y_true - y_pred)) 
    SS_tot = K.sum(K.square(y_true - K.mean(y_true))) 
    return ( 1 - SS_res/(SS_tot + K.epsilon()) )


In [12]:

model = Sequential()
model.add(Dense(8, input_dim=2, activation='relu',
                    name='main_input'))
model.add(Dense(10,activation='relu',name='layer_1'))
model.add(Dense(20,activation='relu',
                    name='layer_2'))
    
model.add(Dense(40,activation='relu'
                    ,name='layer_3'))
model.add(Dense(10,activation='relu',
                    name='layer_4'))

model.add(Dense(1,name='layer_output'))



adam = tf.keras.optimizers.Adam(learning_rate=0.001)

model.compile(loss='mean_squared_error', optimizer=adam,metrics=['mse','mae',r_square])

callbacks = [
    EarlyStopping(
        monitor='val_loss', 
        patience=5500,
        mode='min',verbose=1),
    ModelCheckpoint('assets/ann_model.h5',
        monitor='val_r_square', 
        save_best_only=True, 
        mode='max',verbose=2)]

hist = model.fit(X_train,y_train,epochs=10000,callbacks=callbacks,batch_size=32,validation_data=(X_test,y_test)
                ,shuffle=True)


Epoch 1/10000
 1/22 [>.............................] - ETA: 0s - loss: 0.0012 - mse: 0.0012 - mae: 0.0251 - r_square: -16863.4941
Epoch 00001: val_r_square improved from -inf to -747.06000, saving model to /home/kareem/testing.h5
22/22 [==============================] - 0s 16ms/step - loss: 2.7326e-04 - mse: 2.7326e-04 - mae: 0.0110 - r_square: -3237.0454 - val_loss: 3.7632e-05 - val_mse: 3.7632e-05 - val_mae: 0.0049 - val_r_square: -747.0600
Epoch 2/10000
21/22 [===========================>..] - ETA: 0s - loss: 2.0723e-05 - mse: 2.0723e-05 - mae: 0.0033 - r_square: -276.6973
Epoch 00002: val_r_square improved from -747.06000 to -149.54742, saving model to /home/kareem/testing.h5
22/22 [==============================] - 0s 6ms/step - loss: 2.0046e-05 - mse: 2.0046e-05 - mae: 0.0033 - r_square: -266.2413 - val_loss: 6.5532e-06 - val_mse: 6.5532e-06 - val_mae: 0.0020 - val_r_square: -149.5474
Epoch 3/10000
22/22 [==============================] - ETA: 0s - loss: 5.1858e-06 - mse: 5.1858e

Epoch 19/10000
 1/22 [>.............................] - ETA: 0s - loss: 1.0402e-07 - mse: 1.0402e-07 - mae: 2.2997e-04 - r_square: -0.9029
Epoch 00019: val_r_square did not improve from -4.12979
22/22 [==============================] - 0s 4ms/step - loss: 3.0080e-07 - mse: 3.0080e-07 - mae: 3.4815e-04 - r_square: -3.1323 - val_loss: 2.9565e-07 - val_mse: 2.9565e-07 - val_mae: 3.2806e-04 - val_r_square: -5.6100
Epoch 20/10000
16/22 [====================>.........] - ETA: 0s - loss: 2.6426e-07 - mse: 2.6426e-07 - mae: 3.3372e-04 - r_square: -2.6075
Epoch 00020: val_r_square did not improve from -4.12979
22/22 [==============================] - 0s 5ms/step - loss: 2.4774e-07 - mse: 2.4774e-07 - mae: 3.1672e-04 - r_square: -2.2853 - val_loss: 2.8160e-07 - val_mse: 2.8160e-07 - val_mae: 2.7703e-04 - val_r_square: -5.4125
Epoch 21/10000
 1/22 [>.............................] - ETA: 0s - loss: 1.0754e-07 - mse: 1.0754e-07 - mae: 2.1634e-04 - r_square: -0.2048
Epoch 00021: val_r_square did not

 1/22 [>.............................] - ETA: 0s - loss: 5.4609e-08 - mse: 5.4609e-08 - mae: 1.7974e-04 - r_square: 0.2845
Epoch 00038: val_r_square did not improve from -0.93493
22/22 [==============================] - 0s 3ms/step - loss: 8.3431e-08 - mse: 8.3431e-08 - mae: 1.8706e-04 - r_square: -0.0408 - val_loss: 9.1926e-08 - val_mse: 9.1926e-08 - val_mae: 1.9008e-04 - val_r_square: -1.1590
Epoch 39/10000
 1/22 [>.............................] - ETA: 0s - loss: 1.2536e-07 - mse: 1.2536e-07 - mae: 2.1094e-04 - r_square: -1.7012
Epoch 00039: val_r_square did not improve from -0.93493
22/22 [==============================] - 0s 3ms/step - loss: 1.4914e-07 - mse: 1.4914e-07 - mae: 2.4792e-04 - r_square: -0.9599 - val_loss: 1.5568e-07 - val_mse: 1.5568e-07 - val_mae: 2.6897e-04 - val_r_square: -2.8196
Epoch 40/10000
17/22 [======================>.......] - ETA: 0s - loss: 1.5789e-07 - mse: 1.5789e-07 - mae: 2.6411e-04 - r_square: -1.0851
Epoch 00040: val_r_square did not improve from -0

Epoch 58/10000
18/22 [=======================>......] - ETA: 0s - loss: 1.1439e-07 - mse: 1.1439e-07 - mae: 2.3366e-04 - r_square: -0.4013
Epoch 00058: val_r_square improved from -0.51671 to -0.43712, saving model to /home/kareem/testing.h5
22/22 [==============================] - 0s 8ms/step - loss: 1.0818e-07 - mse: 1.0818e-07 - mae: 2.2746e-04 - r_square: -0.3176 - val_loss: 6.8101e-08 - val_mse: 6.8101e-08 - val_mae: 1.7763e-04 - val_r_square: -0.4371
Epoch 59/10000
 1/22 [>.............................] - ETA: 0s - loss: 2.5741e-08 - mse: 2.5741e-08 - mae: 1.2246e-04 - r_square: 0.7026
Epoch 00059: val_r_square did not improve from -0.43712
22/22 [==============================] - 0s 5ms/step - loss: 5.9422e-08 - mse: 5.9422e-08 - mae: 1.6743e-04 - r_square: 0.2846 - val_loss: 8.5000e-08 - val_mse: 8.5000e-08 - val_mae: 1.8787e-04 - val_r_square: -0.8300
Epoch 60/10000
 1/22 [>.............................] - ETA: 0s - loss: 1.2050e-07 - mse: 1.2050e-07 - mae: 2.2560e-04 - r_squar

Epoch 78/10000
 1/22 [>.............................] - ETA: 0s - loss: 6.0719e-08 - mse: 6.0719e-08 - mae: 1.6488e-04 - r_square: 0.4498
Epoch 00078: val_r_square did not improve from -0.18410
22/22 [==============================] - 0s 4ms/step - loss: 7.3044e-08 - mse: 7.3044e-08 - mae: 1.9711e-04 - r_square: 0.1009 - val_loss: 8.7556e-08 - val_mse: 8.7556e-08 - val_mae: 2.1224e-04 - val_r_square: -0.9439
Epoch 79/10000
 1/22 [>.............................] - ETA: 0s - loss: 8.4852e-08 - mse: 8.4852e-08 - mae: 2.1779e-04 - r_square: -0.0568
Epoch 00079: val_r_square did not improve from -0.18410
22/22 [==============================] - 0s 3ms/step - loss: 7.2774e-08 - mse: 7.2774e-08 - mae: 1.8322e-04 - r_square: 0.0474 - val_loss: 7.0700e-08 - val_mse: 7.0700e-08 - val_mae: 1.8685e-04 - val_r_square: -0.6790
Epoch 80/10000
22/22 [==============================] - ETA: 0s - loss: 6.2800e-08 - mse: 6.2800e-08 - mae: 1.7373e-04 - r_square: 0.1917
Epoch 00080: val_r_square did not imp

...

Epoch 9914/10000
 1/22 [>.............................] - ETA: 0s - loss: 7.7504e-10 - mse: 7.7504e-10 - mae: 2.6552e-05 - r_square: 0.9931
Epoch 09914: val_r_square did not improve from 0.99978
22/22 [==============================] - 0s 5ms/step - loss: 8.1690e-10 - mse: 8.1690e-10 - mae: 2.4786e-05 - r_square: 0.9900 - val_loss: 4.5833e-11 - val_mse: 4.5833e-11 - val_mae: 5.4294e-06 - val_r_square: 0.9988
Epoch 9915/10000
 1/22 [>.............................] - ETA: 0s - loss: 4.3840e-11 - mse: 4.3840e-11 - mae: 5.5128e-06 - r_square: 0.9992
Epoch 09915: val_r_square did not improve from 0.99978
22/22 [==============================] - 0s 4ms/step - loss: 3.7180e-10 - mse: 3.7180e-10 - mae: 1.5646e-05 - r_square: 0.9950 - val_loss: 3.7664e-10 - val_mse: 3.7664e-10 - val_mae: 1.8537e-05 - val_r_square: 0.9915
Epoch 9916/10000
 1/22 [>.............................] - ETA: 0s - loss: 3.7073e-10 - mse: 3.7073e-10 - mae: 1.8673e-05 - r_square: 0.9963
Epoch 09916: val_r_square did not im

Epoch 9934/10000
 1/22 [>.............................] - ETA: 0s - loss: 2.2328e-10 - mse: 2.2328e-10 - mae: 1.2746e-05 - r_square: 0.9984
Epoch 09934: val_r_square did not improve from 0.99978
22/22 [==============================] - 0s 4ms/step - loss: 5.1179e-10 - mse: 5.1179e-10 - mae: 1.9858e-05 - r_square: 0.9923 - val_loss: 7.1795e-10 - val_mse: 7.1795e-10 - val_mae: 2.6037e-05 - val_r_square: 0.9848
Epoch 9935/10000
 1/22 [>.............................] - ETA: 0s - loss: 7.0713e-10 - mse: 7.0713e-10 - mae: 2.5811e-05 - r_square: 0.9926
Epoch 09935: val_r_square did not improve from 0.99978
22/22 [==============================] - 0s 4ms/step - loss: 4.6536e-10 - mse: 4.6536e-10 - mae: 1.6726e-05 - r_square: 0.9941 - val_loss: 1.3115e-10 - val_mse: 1.3115e-10 - val_mae: 1.0523e-05 - val_r_square: 0.9970
Epoch 9936/10000
15/22 [===================>..........] - ETA: 0s - loss: 1.8129e-10 - mse: 1.8129e-10 - mae: 1.1493e-05 - r_square: 0.9975
Epoch 09936: val_r_square did not im

Epoch 9954/10000
21/22 [===========================>..] - ETA: 0s - loss: 1.1905e-09 - mse: 1.1905e-09 - mae: 2.8291e-05 - r_square: 0.9830
Epoch 09954: val_r_square did not improve from 0.99978
22/22 [==============================] - 0s 5ms/step - loss: 1.1589e-09 - mse: 1.1589e-09 - mae: 2.7925e-05 - r_square: 0.9836 - val_loss: 8.9371e-10 - val_mse: 8.9371e-10 - val_mae: 2.9242e-05 - val_r_square: 0.9803
Epoch 9955/10000
 1/22 [>.............................] - ETA: 0s - loss: 8.8736e-10 - mse: 8.8736e-10 - mae: 2.8602e-05 - r_square: 0.9912
Epoch 09955: val_r_square did not improve from 0.99978
22/22 [==============================] - 0s 4ms/step - loss: 7.0208e-10 - mse: 7.0208e-10 - mae: 2.0792e-05 - r_square: 0.9909 - val_loss: 2.2672e-09 - val_mse: 2.2672e-09 - val_mae: 4.7165e-05 - val_r_square: 0.9505
Epoch 9956/10000
 1/22 [>.............................] - ETA: 0s - loss: 2.1575e-09 - mse: 2.1575e-09 - mae: 4.5985e-05 - r_square: 0.9724
Epoch 09956: val_r_square did not im

Epoch 9974/10000
 1/22 [>.............................] - ETA: 0s - loss: 1.2266e-10 - mse: 1.2266e-10 - mae: 1.0054e-05 - r_square: 0.9973
Epoch 09974: val_r_square did not improve from 0.99978
22/22 [==============================] - 0s 4ms/step - loss: 1.7959e-10 - mse: 1.7959e-10 - mae: 1.1153e-05 - r_square: 0.9976 - val_loss: 5.8021e-11 - val_mse: 5.8021e-11 - val_mae: 5.7298e-06 - val_r_square: 0.9986
Epoch 9975/10000
22/22 [==============================] - ETA: 0s - loss: 5.5255e-10 - mse: 5.5255e-10 - mae: 2.0775e-05 - r_square: 0.9922
Epoch 09975: val_r_square did not improve from 0.99978
22/22 [==============================] - 0s 5ms/step - loss: 5.5255e-10 - mse: 5.5255e-10 - mae: 2.0775e-05 - r_square: 0.9922 - val_loss: 7.7005e-10 - val_mse: 7.7005e-10 - val_mae: 2.7122e-05 - val_r_square: 0.9830
Epoch 9976/10000
 1/22 [>.............................] - ETA: 0s - loss: 6.5464e-10 - mse: 6.5464e-10 - mae: 2.5158e-05 - r_square: 0.9911
Epoch 09976: val_r_square did not im

Epoch 9994/10000
 1/22 [>.............................] - ETA: 0s - loss: 2.8755e-11 - mse: 2.8755e-11 - mae: 4.3744e-06 - r_square: 0.9980
Epoch 09994: val_r_square did not improve from 0.99978
22/22 [==============================] - 0s 4ms/step - loss: 2.4296e-10 - mse: 2.4296e-10 - mae: 1.1819e-05 - r_square: 0.9974 - val_loss: 8.0555e-10 - val_mse: 8.0555e-10 - val_mae: 2.7840e-05 - val_r_square: 0.9826
Epoch 9995/10000
 1/22 [>.............................] - ETA: 0s - loss: 8.0708e-10 - mse: 8.0708e-10 - mae: 2.7747e-05 - r_square: 0.9892
Epoch 09995: val_r_square did not improve from 0.99978
22/22 [==============================] - 0s 3ms/step - loss: 6.1247e-10 - mse: 6.1247e-10 - mae: 2.0242e-05 - r_square: 0.9911 - val_loss: 5.9035e-10 - val_mse: 5.9035e-10 - val_mae: 2.3597e-05 - val_r_square: 0.9871
Epoch 9996/10000
 1/22 [>.............................] - ETA: 0s - loss: 5.9320e-10 - mse: 5.9320e-10 - mae: 2.4017e-05 - r_square: 0.9846
Epoch 09996: val_r_square did not im

In [27]:
model.summary()

Model: "sequential_3"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
main_input (Dense)           (None, 8)                 24        
_________________________________________________________________
layer_1 (Dense)              (None, 10)                90        
_________________________________________________________________
layer_2 (Dense)              (None, 20)                220       
_________________________________________________________________
layer_3 (Dense)              (None, 40)                840       
_________________________________________________________________
layer_4 (Dense)              (None, 10)                410       
_________________________________________________________________
layer_output (Dense)         (None, 1)                 11        
Total params: 1,595
Trainable params: 1,595
Non-trainable params: 0
____________________________________________________

In [16]:
from tensorflow.keras.models import load_model

m = load_model('assets/testing.h5',custom_objects={'r_square': r_square},compile=True) 

In [18]:
m.get_config()

{'name': 'sequential_3',
 'layers': [{'class_name': 'Dense',
   'config': {'name': 'main_input',
    'trainable': True,
    'batch_input_shape': (None, 2),
    'dtype': 'float32',
    'units': 8,
    'activation': 'relu',
    'use_bias': True,
    'kernel_initializer': {'class_name': 'GlorotUniform',
     'config': {'seed': None}},
    'bias_initializer': {'class_name': 'Zeros', 'config': {}},
    'kernel_regularizer': None,
    'bias_regularizer': None,
    'activity_regularizer': None,
    'kernel_constraint': None,
    'bias_constraint': None}},
  {'class_name': 'Dense',
   'config': {'name': 'layer_1',
    'trainable': True,
    'dtype': 'float32',
    'units': 10,
    'activation': 'relu',
    'use_bias': True,
    'kernel_initializer': {'class_name': 'GlorotUniform',
     'config': {'seed': None}},
    'bias_initializer': {'class_name': 'Zeros', 'config': {}},
    'kernel_regularizer': None,
    'bias_regularizer': None,
    'activity_regularizer': None,
    'kernel_constraint': 

In [17]:
r = m.predict(X_test)
r2(y_test,r),mse(y_test,r)

(0.9998328828416478, 1.0897568335082298e-11)